In [10]:
%pip install getdaft folium bloxs --q

Note: you may need to restart the kernel to use updated packages.


In [11]:
import daft
from bloxs import B
import altair as alt 
import polars as pl
from daft.expressions import col
import pandas as pd
import ipywidgets as widgets
import folium
from folium.plugins import HeatMap, MarkerCluster
from IPython.display import display, HTML, clear_output, Markdown
import requests
from powerbiclient import QuickVisualize, get_dataset_config
import numpy as np
import json
import pyarrow.parquet as pq
from pyarrow import fs
import pyarrow.dataset as ds
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

"""
Reference : 
https://location.foursquare.com/resources/blog/products/foursquare-open-source-places-a-new-foundational-dataset-for-the-geospatial-community/

https://simonwillison.net/search/?q=foursquare

"""
#initialize daft 
daft.context.set_runner_native()

# Scan data from S3
path = "s3://fsq-os-places-us-east-1/release/dt=2024-11-19/places/**"
IO_CONFIG = daft.io.IOConfig(s3=daft.io.S3Config(anonymous=True))
df = daft.read_parquet(
   path, 
   io_config=IO_CONFIG,
   schema={
       'date_created': daft.DataType.date(),
       'date_refreshed': daft.DataType.date(),
       'date_closed': daft.DataType.date()
   }
)

## Daft UDF to make name Title Case and normalize names
@daft.udf(return_dtype=daft.DataType.string())
def to_title_case(x: daft.Series) -> list:
    values = x.to_pylist()
    return [v.title() if v is not None else None for v in values]

# filter and transform
us_coffee_df = df.where(
    (col("country") == "US") & ##US only
    ((col("name").str.lower().str.contains("coffee")) | 
     (col("name").str.lower().str.contains("roaster"))) & ##some roasters also serve coffee
    (~col("name").str.lower().str.contains("starbucks"))  ## Starbucks sucks
).with_column("name", 
    col("name").str.replace(" and ", " & ")
              .str.replace(" AND ", " & ")
              .str.replace(" And ", " & ")
              .str.replace("'", "")
).with_column("name", to_title_case(col("name")))

#polars df, from daft to use altair
dfarrow = us_coffee_df.select("name","latitude","longitude", "locality","region","postcode", "address","date_closed").to_arrow()
polarsdf = pl.from_arrow(dfarrow )

# pandas df for rest of the analysis using Folium
df_pd = us_coffee_df.select("name","latitude","longitude", "locality","region","postcode", "address","date_closed").to_pandas()
df_pd['date_closed'] = pd.to_datetime(df_pd['date_closed'])

total_rows = df.count().collect().to_pandas()['count'].max()
us_coffee_shops = len(df_pd)
pdx_df = df_pd.query('region == "OR" & locality == "Portland"')
pdx_coffee_shops = len(pdx_df)


displayHTML("""

<div style="font-family: Arial, sans-serif; text-align: center; padding: 20px; background-color: #f0f8ff; border-radius: 10px; box-shadow: 0 4px 8px rgba(0, 0, 0, 0.1);">
    <h1 style="color: #333;">FourSquare Places Data</h1>
    <p style="color: #666; font-size: 18px;">A quick exploration of ☕Coffee Shops in the US and in Portland, OR</p>
</div>
"""

)

B([
    B(total_rows, "Total #Places"),
    B(us_coffee_shops, "#Coffee Shops in the US"),
    B(pdx_coffee_shops , "#Coffee Shops in Portland, OR"),
])

In [12]:
# Get the top 5 coffee shop chains by count
top_5_chains = df_pd.groupby('name').size().nlargest(5)

# Display title
displayHTML("""
<div style="font-family: Arial, sans-serif; text-align: center; padding: 20px; background-color: #f0f8ff; border-radius: 10px; box-shadow: 0 4px 8px rgba(0, 0, 0, 0.1);">
    <h1 style="color: #333;">Top 5 Coffee Chains By Location Count</h1>
    <p style="color: #666; font-size: 18px;">Explore them interactively on a map. I never heard of Dutch Bros in Chicago, make sense looks like they are primarly in the lower US and in the PNW</p>
</div>
""")

# Generate summary statistics
markdown_content = ""
for name, count in top_5_chains.items():
    total_locs = len(df_pd[df_pd['name'] == name])
    valid_locs = len(df_pd[df_pd['name'] == name].dropna(subset=['latitude', 'longitude']))
    regions = df_pd[df_pd['name'] == name]['region'].nunique()
    
    markdown_content += f"""
### {name}
- Total Locations: **{total_locs}**
- Mapped Locations: **{valid_locs}**
- States Present: **{regions}**
"""

display(Markdown(markdown_content))

# Create dropdown options once
options = [(f"{name} ({count} locations)", name) for name, count in top_5_chains.items()]

# Create dropdown widget
dropdown = widgets.Dropdown(
    options=options,
    value=options[0][1],  # Select first chain by default
    description='Select Chain:',
    style={'description_width': 'initial'},
    layout={'width': 'auto'}
)

def create_map(selected_chain):
    # Filter data
    chain_locations = df_pd[df_pd['name'] == selected_chain].copy()
    chain_locations = chain_locations.dropna(subset=['latitude', 'longitude'])
    
    # Calculate center of locations 
    center_lat = chain_locations['latitude'].mean()
    center_lon = chain_locations['longitude'].mean()
    
    # Create base map
    m = folium.Map(location=[center_lat, center_lon], zoom_start=4)
    marker_cluster = MarkerCluster().add_to(m)
    
    # Add markers for all locations of selected chain
    for _, location in chain_locations.iterrows():
        # Create popup content
        popup_content = f"""
        <div style='width: 200px'>
            <b>{location['name']}</b><br>
            Address: {location.get('address', 'N/A')}<br>
            {location.get('locality', 'N/A')}, {location.get('region', 'N/A')} {location.get('postcode', 'N/A')}
        </div>
        """
        
        # Add marker
        folium.Marker(
            location=[float(location['latitude']), float(location['longitude'])],
            popup=folium.Popup(popup_content, max_width=300),
            icon=folium.Icon(color='red', icon='info-sign')
        ).add_to(marker_cluster)
    
    return m

def on_change(change):
    if change['type'] == 'change' and change['name'] == 'value':
        clear_output(wait=True)
        
        selected_chain = change['new']
        chain_locations = df_pd[df_pd['name'] == selected_chain]
        valid_locations = chain_locations.dropna(subset=['latitude', 'longitude'])
        
        print(f"\nShowing {len(valid_locations)} locations (out of {len(chain_locations)} total) for {selected_chain}")
        print(f"Note: {len(chain_locations) - len(valid_locations)} locations excluded due to missing coordinates")
        
        display(dropdown)
        display(create_map(selected_chain))

# Set up callback
dropdown.observe(on_change)

# Initial display
initial_chain = options[0][1]
chain_locations = df_pd[df_pd['name'] == initial_chain]
valid_locations = chain_locations.dropna(subset=['latitude', 'longitude'])

print(f"\nShowing {len(valid_locations)} locations (out of {len(chain_locations)} total) for {initial_chain}")
print(f"Note: {len(chain_locations) - len(valid_locations)} locations excluded due to missing coordinates")

display(dropdown)
display(create_map(initial_chain))


### Peets Coffee & Tea
- Total Locations: **1150**
- Mapped Locations: **1143**
- States Present: **42**

### Dutch Bros Coffee
- Total Locations: **984**
- Mapped Locations: **983**
- States Present: **19**

### Caribou Coffee
- Total Locations: **898**
- Mapped Locations: **896**
- States Present: **30**

### Biggby Coffee
- Total Locations: **615**
- Mapped Locations: **564**
- States Present: **16**

### Scooters Coffee
- Total Locations: **578**
- Mapped Locations: **574**
- States Present: **33**



Showing 1143 locations (out of 1150 total) for Peets Coffee & Tea
Note: 7 locations excluded due to missing coordinates


Dropdown(description='Select Chain:', layout=Layout(width='auto'), options=(('Peets Coffee & Tea (1150 locatio…

In [13]:
displayHTML("""
<div style="font-family: Arial, sans-serif; text-align: center; padding: 20px; background-color: #f0f8ff; border-radius: 10px; box-shadow: 0 4px 8px rgba(0, 0, 0, 0.1);">
    <h1 style="color: #333;">Open vs Closed For these 5 chains</h1>
    <p style="color: #666; font-size: 18px;">I remember Caribou Coffee being closed many years ago. This data may be outdated but looks like a large number of them are closed.</p>
</div>
""")

# Get top 5 chains
top_5_chains = (polarsdf
    .group_by('name')
    .agg(pl.len().alias('count'))  # Using agg instead of count
    .sort('count', descending=True)
    .head(5)
)
top_five = top_5_chains['name'].to_list()

#using Polars
status_data = (
    polarsdf
    .filter(pl.col('name').is_in(top_five))
    .select(['name', 'date_closed'])
    .with_columns(
        status=pl.when(pl.col('date_closed').is_null())
              .then(pl.lit('Open'))
              .otherwise(pl.lit('Closed'))
    )
    .group_by(['name', 'status'])
    .agg(pl.len().alias('count'))
    .sort('name')
)

# plot the data
chart = alt.Chart(status_data).mark_bar().encode(
    x=alt.X('name:N', title='Coffee Chain'),
    y=alt.Y('count:Q', title='Number of Locations'),
    color=alt.Color('status:N', 
                   scale=alt.Scale(domain=['Open', 'Closed'],
                                 range=['#4A2C2A', '#D4B59D'])),
    tooltip=[
        alt.Tooltip('name:N', title='Chain'),
        alt.Tooltip('status:N', title='Status'),
        alt.Tooltip('count:Q', title='Count')
    ]
).properties(
    title='Open vs Closed Locations by Coffee Chain',
    width=600,
    height=400
).configure_axis(
    labelAngle=45
)

display(chart)



alt.Chart(...)

In [14]:
displayHTML("""
<div style="font-family: Arial, sans-serif; text-align: center; padding: 20px; background-color: #f0f8ff; border-radius: 10px; box-shadow: 0 4px 8px rgba(0, 0, 0, 0.1);">
    <h1 style="color: #333;">Where are these coffee shops in the US?</h1>
    <p style="color: #666; font-size: 18px;">California, Seattle, NY, Florida, Texas, Oregon stand out</p>
</div>
""")

state_counts = df_pd['region'].value_counts().to_dict()

# Get US state GeoJSON
url = "https://raw.githubusercontent.com/python-visualization/folium/master/examples/data/us-states.json"
us_states = requests.get(url).json()

# Create base map
m = folium.Map(
    location=[39.8283, -98.5795],
    zoom_start=4,
    tiles='cartodbpositron'
)

# Add choropleth layer
folium.Choropleth(
    geo_data=us_states,
    name='Coffee Shops by State',
    data=state_counts,
    columns=['State', 'Count'],
    key_on='feature.id',
    fill_color='BuGn', 
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Number of Coffee Shops',
    highlight=True
).add_to(m)

# Add hover
folium.LayerControl().add_to(m)

display(m)

In [15]:
displayHTML("""
<div style="font-family: Arial, sans-serif; text-align: center; padding: 20px; background-color: #f0f8ff; border-radius: 10px; box-shadow: 0 4px 8px rgba(0, 0, 0, 0.1);">
    <h1 style="color: #333;">Distribution of Coffee Shops</h1>
    <p style="color: #666; font-size: 18px;">Eastern half has way more shops than the Western half but East also accounts for ~80% of US population</p>
</div>
""")

# Prepare heat map data
heat_data = [[row['latitude'], row['longitude']] for _, row in df_pd.iterrows() 
             if pd.notna(row['latitude']) and pd.notna(row['longitude'])]

# Create different base map layers
base_layers = {
    'Default': folium.TileLayer(
        tiles='OpenStreetMap',
        name='Default Map',
        attr='© OpenStreetMap contributors'
    ),
    'Black & White': folium.TileLayer(
        tiles='CartoDB positron',
        name='B&W Map',
        attr='© CartoDB | © OpenStreetMap contributors'
    ),
    'Dark': folium.TileLayer(
        tiles='CartoDB dark_matter',
        name='Dark Map',
        attr='© CartoDB | © OpenStreetMap contributors'
    ),
    'Minimal': folium.TileLayer(
        tiles='Stamen Toner',
        name='Minimal Map',
        attr='© Stamen Design | © OpenStreetMap contributors'
    )
}


m = folium.Map(location=[39.8283, -98.5795], 
               zoom_start=4,
               tiles=None) 

# Add all base layers to the map
for layer in base_layers.values():
    layer.add_to(m)

# Set the default layer
base_layers['Default'].add_to(m)

# Create heatmap layer
heatmap_layer = HeatMap(
    heat_data,
    radius=5,
    blur=5,
    max_zoom=1,
    gradient={
        0.2: '#fff5c6',  
        0.4: '#ffd780',  
        0.6: '#ff9b57',
        0.8: '#da4c5f',
        1.0: '#5c1a33'
    },
    name='Heat Map'
)
heatmap_layer.add_to(m)

# Add layer control
folium.LayerControl(position='topright').add_to(m)

display(m)

In [16]:
displayHTML("""
<div style="font-family: Arial, sans-serif; text-align: center; padding: 20px; background-color: #f0f8ff; border-radius: 10px; box-shadow: 0 4px 8px rgba(0, 0, 0, 0.1);">
    <h1 style="color: #333;">Where Can I find coffee in Portland, OR?</h1>
    <p style="color: #666; font-size: 18px;">Portland has the best coffee shops, no questions! Sorry Seattle 😁</p>
</div>
""")

m = folium.Map(location=[45.52, -122.67], zoom_start=13) #portland lang/lat

for _, row in pdx_df.iterrows():
   if pd.notna(row['latitude']) and pd.notna(row['longitude']):
       folium.Marker(
           location=[row['latitude'], row['longitude']],
           popup=f"{row['name']}<br>{row['address']}",
           icon=folium.Icon(color='brown', icon='info-sign')
       ).add_to(m)

display(m)

/tmp/ipykernel_66/3490346584.py:15: UserWarning:

color argument of Icon should be one of: {'purple', 'green', 'orange', 'darkblue', 'lightred', 'red', 'darkpurple', 'white', 'gray', 'beige', 'blue', 'lightblue', 'black', 'lightgray', 'darkgreen', 'cadetblue', 'darkred', 'pink', 'lightgreen'}.



In [17]:
from IPython.display import display, HTML

html_header = """
<div style="font-family: Arial, sans-serif; text-align: center; padding: 20px; background-color: #f0f8ff; border-radius: 10px; box-shadow: 0 4px 8px rgba(0, 0, 0, 0.1);">
    <h1 style="color: #333;">Which shops have closed & when in the last 4 years?</h1>
    <p style="color: #666; font-size: 18px;"></p>
</div>
"""
display(HTML(html_header))

df_pd['date_closed'] = pd.to_datetime(df_pd['date_closed'], errors='coerce')
df_recent = df_pd[df_pd['date_closed'].dt.year > 2020].copy()
closed_shops = df_recent[df_recent['date_closed'].notna()].copy()
closed_shops['year_month'] = closed_shops['date_closed'].dt.to_period('M')
top_10_states = closed_shops['region'].value_counts().head(10).index
state_data = closed_shops[closed_shops['region'].isin(top_10_states)].copy()

monthly_chain_data = state_data.groupby(['year_month', 'region', 'name']).size().reset_index(name='chain_closures')
monthly_chain_data = monthly_chain_data.sort_values('chain_closures', ascending=False)

def get_top_chains(group):
    chain_info = group.groupby('name')['chain_closures'].sum().sort_values(ascending=False).head(5)
    return '<br>'.join([f"{name}: {count} locations" for name, count in chain_info.items()])


monthly_closures = monthly_chain_data.groupby(['year_month', 'region'])['chain_closures'].sum().reset_index()
chain_details = monthly_chain_data.groupby(['year_month', 'region']).apply(get_top_chains).reset_index()
chain_details.columns = ['year_month', 'region', 'chain_details']
monthly_closures = monthly_closures.merge(chain_details, on=['year_month', 'region'])
monthly_closures['year_month'] = pd.to_datetime(monthly_closures['year_month'].astype(str))

fig = px.line(monthly_closures, 
              x='year_month', 
              y='chain_closures',
              color='region',
              title='Coffee Shop Closures by State (Top 10 States)',
              labels={
                  'year_month': 'Date',
                  'chain_closures': 'Number of Closures',
                  'region': 'State'
              },
              custom_data=['chain_details'])

# Update layout
fig.update_layout(
    plot_bgcolor='white',
    paper_bgcolor='white',
    font=dict(size=12),
    legend=dict(
        yanchor="top",
        y=0.99,
        xanchor="left",
        x=1.02
    ),
    hovermode='x unified',
    xaxis=dict(
        gridcolor='lightgray',
        title_font=dict(size=14),
        tickfont=dict(size=12)
    ),
    yaxis=dict(
        gridcolor='lightgray',
        title_font=dict(size=14),
        tickfont=dict(size=12)
    )
)


fig.update_traces(
    hovertemplate="<b>%{y}</b> total closures<br>%{x|%B %Y}<br><br>Top 5 Chains:<br>%{customdata[0]}<extra></extra>"
)

fig.show()

In [18]:
## list of files

s3 = fs.S3FileSystem(region='us-east-1')
path = "s3://fsq-os-places-us-east-1/release/dt=2024-11-19/places/*.parquet"


file_info = s3.get_file_info(fs.FileSelector(
    "fsq-os-places-us-east-1/release/dt=2024-11-19/",
    recursive=True
))
for info in file_info:
    print(info.path)

fsq-os-places-us-east-1/release/dt=2024-11-19/categories/parquet/categories.snappy.parquet
fsq-os-places-us-east-1/release/dt=2024-11-19/categories/parquet
fsq-os-places-us-east-1/release/dt=2024-11-19/categories
fsq-os-places-us-east-1/release/dt=2024-11-19/places/parquet/places-00000.snappy.parquet
fsq-os-places-us-east-1/release/dt=2024-11-19/places/parquet
fsq-os-places-us-east-1/release/dt=2024-11-19/places
fsq-os-places-us-east-1/release/dt=2024-11-19/places/parquet/places-00001.snappy.parquet
fsq-os-places-us-east-1/release/dt=2024-11-19/places/parquet/places-00002.snappy.parquet
fsq-os-places-us-east-1/release/dt=2024-11-19/places/parquet/places-00003.snappy.parquet
fsq-os-places-us-east-1/release/dt=2024-11-19/places/parquet/places-00004.snappy.parquet
fsq-os-places-us-east-1/release/dt=2024-11-19/places/parquet/places-00005.snappy.parquet
fsq-os-places-us-east-1/release/dt=2024-11-19/places/parquet/places-00006.snappy.parquet
fsq-os-places-us-east-1/release/dt=2024-11-19/plac